# Calculating the population living outside a 10-minute drive of a pharmacy

This notebook calculates the population living inside and outside a 10-minute drive from a pharmacy. Isochrones generated around pharmacies open in June 2017 and June 2022 provide the total area within the 10-minute driving range. The five-year American Community Survey was used for population data by census tract. The population data was used to estimate the population living within the total isochrone area.

The isochrones were generated in a separate notebook, then converted from geojsons to shapefiles using [mapshaper.org](http://mapshaper.org) before being loaded in here. For the 2022 analysis, 2020 ACS data and 2021 Census Tract data were used because they are the most recent available.

In [1]:
import altair as alt
import numpy as np
import pandas as pd
import geopandas as gpd
import cenpy as cen
from shapely.geometry import Point, Polygon, linestring, shape, mapping
from getpass import getpass

In [2]:
isochrones22 = gpd.read_file('data/active_driving_isochrones_10min.zip')
isochrones17 = gpd.read_file('data/2017_driving_isochrones_10min.zip')

In [3]:
isochrones22 = isochrones22.dissolve()
isochrones17 = isochrones17.dissolve()

In [4]:
alt.Chart(isochrones22).mark_geoshape()

alt.Chart(...)

In [5]:
alt.Chart(isochrones17).mark_geoshape()

alt.Chart(...)

## Pulling population data from the Census API

In [6]:
nyc_fips = ['005', '047', '061', '081']

In [7]:
CENSUS_API_KEY = getpass('Enter Census API Key: ')

Enter Census API Key: ········


In [8]:
con = cen.remote.APIConnection('ACSDT5Y2020',apikey=CENSUS_API_KEY)

columns = [
    'B01003_001' # Total Population
]

columns_E = [i+'E' for i in columns]
columns_M = [i+'M' for i in columns]

g_unit = 'tract'
g_filter = {'state':'36'} 

tract_pop_20 = con.query(columns_E + columns_M, geo_unit=g_unit, geo_filter=g_filter)

In [9]:
con = cen.remote.APIConnection('ACSDT5Y2017',apikey=CENSUS_API_KEY)
tract_pop_17 = con.query(columns_E + columns_M, geo_unit=g_unit, geo_filter=g_filter)

In [10]:
tracts21 = gpd.read_file('data/tl_2021_36_tract/')
tracts17 = gpd.read_file('data/tl_2017_36_tract/')

In [11]:
tract_pop_20['GEOID'] = tract_pop_20.state + tract_pop_20.county + tract_pop_20.tract
tract_pop_17['GEOID'] = tract_pop_17.state + tract_pop_17.county + tract_pop_17.tract

In [12]:
tract_pop_20 = tracts21.merge(tract_pop_20, on='GEOID')
tract_pop_17 = tracts17.merge(tract_pop_17, on='GEOID')

In [13]:
# Exclude NYC
tract_pop_20 = tract_pop_20.query('county.isin(@nyc_fips) == False')
tract_pop_17 = tract_pop_17.query('county.isin(@nyc_fips) == False')

In [14]:
tract_pop_20.head(1)

STATEFP COUNTYFP TRACTCE        GEOID NAME         NAMELSAD  MTFCC FUNCSTAT  \
6      36      119  007200  36119007200   72  Census Tract 72  G5020        S   

     ALAND   AWATER     INTPTLAT      INTPTLON  \
6  3602393  7956100  +40.9283295  -073.7301900   

                                            geometry B01003_001E B01003_001M  \
6  POLYGON ((-73.74754 40.94401, -73.74669 40.944...        6441         676   

  state county   tract  
6    36    119  007200

## 2022 


In [15]:
tract_pop_20 = tract_pop_20.to_crs('EPSG:5070')

In [16]:
tract_pop_20['area'] = tract_pop_20.area / 10**6

In [17]:
isochrones22 = isochrones22.to_crs('EPSG:5070')

In [18]:
# Population within a 10 minute drive of a pharmacy
popNearPharmacy = gpd.overlay(tract_pop_20, isochrones22, how='intersection')

/var/folders/tx/ryc062z51z1287rjpvrp4jlc0000gn/T/ipykernel_62056/1715179142.py:2: UserWarning: `keep_geom_type=True` in overlay resulted in 3 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  popNearPharmacy = gpd.overlay(tract_pop_20, isochrones22, how='intersection')


In [19]:
popNearPharmacy['area2'] = popNearPharmacy.area / 10**6

In [20]:
popNearPharmacy['proportion'] = popNearPharmacy['area2'] / popNearPharmacy['area']

In [21]:
popNearPharmacy = popNearPharmacy.dropna()
popNearPharmacy = popNearPharmacy[popNearPharmacy['proportion'] > 0] 

In [22]:
popNearPharmacy['B01003_001E'] = popNearPharmacy['B01003_001E'].astype(int)

In [23]:
popNearPharmacy['totalPopulation'] = (popNearPharmacy['proportion'] * popNearPharmacy['B01003_001E']).round().astype(int)

In [24]:
tract_pop_20['B01003_001E'] = tract_pop_20['B01003_001E'].astype(int)

In [25]:
pop_sum = tract_pop_20['B01003_001E'].sum()

In [26]:
population = popNearPharmacy['totalPopulation'].sum()/pop_sum

In [27]:
# Percent of state population living within of a 10 minute drive of a pharmacy (exclude NYC)
population

0.7809978095569393

In [29]:
# Percent of state population living outside of a 10 minute drive of a pharmacy (exclude NYC)
(1 - population) * 100

21.90021904430607

## 2017

In [30]:
tract_pop_17 = tract_pop_17.to_crs('EPSG:5070')

In [31]:
tract_pop_17['area'] = tract_pop_17.area / 10**6

In [32]:
isochrones17 = isochrones17.to_crs('EPSG:5070')

In [33]:
# Population within a 10 minute drive of a pharmacy
popNearPharmacy = gpd.overlay(tract_pop_17, isochrones17, how='intersection', keep_geom_type=False)

In [34]:
popNearPharmacy['area2'] = popNearPharmacy.area / 10**6

In [35]:
popNearPharmacy['proportion'] = popNearPharmacy['area2'] / popNearPharmacy['area']

In [36]:
popNearPharmacy = popNearPharmacy.dropna()
popNearPharmacy = popNearPharmacy[popNearPharmacy['proportion'] > 0] 

In [37]:
popNearPharmacy['B01003_001E'] = popNearPharmacy['B01003_001E'].astype(int)

In [38]:
popNearPharmacy['totalPopulation'] = (popNearPharmacy['proportion'] * popNearPharmacy['B01003_001E']).round().astype(int)

In [39]:
tract_pop_17['B01003_001E'] = tract_pop_17['B01003_001E'].astype(int)


In [40]:
pop_sum = tract_pop_17['B01003_001E'].sum()

In [41]:
population = popNearPharmacy['totalPopulation'].sum()/pop_sum

In [42]:
# Percent of state pop living within of a 10 minute drive of a pharmacy (exclude NYC)
population

0.8450087176962062

In [43]:
# Percent of state pop living outside of a 10 minute drive of a pharmacy (exclude NYC)
(1 - population) * 100

15.499128230379377